In [1]:
import pandas as pd

df = pd.read_csv('raw/bq-results-20211206-133858-irtkgx60el7i.csv').drop(['ParentUrl', 'ParentAuthor', 'ParentTime', 'ParentScore'], axis=1)

# There's a mix of HTML, sanitized links and raw Unicode that we'd like to clean up
df.text = df.text.str.replace('<p>', '\n')
strings_to_remove = ['rel="nofollow"', '<pre>', '</pre>', '<i>', '</i>', '<code>', '</code>', '&gt;']
email_regex = '[a-zA-Z0-9._-]{0,30}@[a-zA-Z0-9._-]{0,20}\.[a-zA-Z0-9_-]{2,3}' # for redacting emails
munged_url_regex = 'http(s)?:\&\#.*?\<\/a>'

for string in strings_to_remove:
    df.text = df.text.str.replace(string, '')


df.text = df.text.replace(email_regex, 'REDACTED_EMAIL', regex=True)
df.text = df.text.replace(munged_url_regex, '', regex=True)

    # fix some unicode issues
df.text = df.text.str.replace('&#x27;', "'")
df.text = df.text.str.replace('&#x2F;', "/")
df.text = df.text.str.replace("&quot;", '"')

hiring_df = df[df.ParentTitle.str.lower().str.contains('who is hiring')]
wants_to_be_hired_df = df[df.ParentTitle.str.lower().str.contains('wants to be hired')]
freelancer_df = df[df.ParentTitle.str.lower().str.contains('freelancer')]


/usr/local/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (4) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [8]:
import datasets
from huggingface_hub import create_repo
from huggingface_hub import Repository

all_datasets = datasets.dataset_dict.DatasetDict({'hiring': datasets.Dataset.from_pandas(hiring_df).remove_columns('__index_level_0__'),
                                                  'wants_to_be_hired': datasets.Dataset.from_pandas(wants_to_be_hired_df).remove_columns('__index_level_0__'),
                                                  'freelancer': datasets.Dataset.from_pandas(freelancer_df).remove_columns('__index_level_0__')})
data_path = './data'
all_datasets.save_to_disk(data_path)

repo_url = 'https://huggingface.co/datasets/dansbecker/hackernews_hiring_posts'
repo = Repository(local_dir=".", clone_from=repo_url)
repo.git_add(data_path)
repo.git_add('*.ipynb')
repo.git_add('README.md')
repo.git_commit("A standard update")